In [1]:
from conllu import parse
from nltk import DependencyGraph
from ufal.udpipe import Model, Pipeline
import re
from transformers import AutoTokenizer
import numpy as np

In [2]:
model = Model.load('russian-ud-2.0-170801.udpipe')

In [9]:
arrParsed = []
longParsed = ''

sent = 'Здравствуйте! До какого числа можно принести аттестат?'
sent = re.sub("\s\s+", ' ', sent)
sent = sent.lower()
sent = sent.replace(u'\xa0', u' ')
sent = sent.strip()
print(sent)
sentS = re.split(";|! |\?|\. ", sent)
sentS = list(filter(None, sentS))

for nSentS in sentS:
    nSentS = re.sub(r'[^\w\s]','', nSentS) 
    
    pipeline = Pipeline(model, 'tokenize', Pipeline.DEFAULT, Pipeline.DEFAULT, Pipeline.DEFAULT)
    parsed = pipeline.process(nSentS)

    # костыли для dependency graph
    parsed = '\n'.join([line for line in parsed.split('\n') if not line.startswith('#')])
    parsed = parsed.replace('\troot\t', '\tROOT\t')
    
    if (len(longParsed) < len(parsed)):
        longParsed = parsed
    
    arrParsed.append(parsed)
arrParsed = list(filter(None, arrParsed))
print(sentS)

здравствуйте! до какого числа можно принести аттестат?
['здравствуйте', 'до какого числа можно принести аттестат']


In [10]:
def get_sov(sent):
    graph = DependencyGraph(tree_str=sent)
    sov = {}
    for triple in graph.triples():
        if triple:
            if triple[0][1] == 'VERB':
                sov[triple[0][0]] = {'subj':'','obj':''}
    for triple in graph.triples():
        if triple:
            if triple[1] == 'nsubj':
                if triple[0][1] == 'VERB':
                    sov[triple[0][0]]['subj']  = triple[2][0]
            if 'obj' in triple[1]:
                if triple[0][1] == 'VERB':
                    sov[triple[0][0]]['obj'] = triple[2][0]
    return sov

In [11]:
arrSov = []
for nArrParsed in arrParsed:
    sov = get_sov(nArrParsed)
    arrSov.append(sov)
arrSov

[{},
 {'можно': {'subj': '', 'obj': ''},
  'принести': {'subj': '', 'obj': 'аттестат'}}]

In [12]:
bigSov = arrSov[0]
if (len(arrSov) > 1):
    for i in range(1, len(arrSov)):
        bigSov = { **bigSov, ** arrSov[i] }

In [14]:
print(bigSov)

{'можно': {'subj': '', 'obj': ''}, 'принести': {'subj': '', 'obj': 'аттестат'}}


In [8]:
tokenizedA = []
if (bigSov == {}):
    arrGraph = []
    graph = DependencyGraph(tree_str=longParsed)
    for i in range(0, len(list(graph.triples()))):
        for j in range(0, len(list(graph.triples())[0])):
            if (list(graph.triples())[i][j][1] == 'NOUN'):
                arrGraph.append(list(graph.triples())[i][j][0])
    arrGraph = set(arrGraph)
print(list(graph.triples()))

NameError: name 'bigSov' is not defined

In [15]:
tokenizer = AutoTokenizer.from_pretrained("cointegrated/rubert-tiny2")

In [16]:
tokenizedA = []
if (bigSov == {}):
    arrGraph = []
    graph = DependencyGraph(tree_str=longParsed)
    for i in range(0, len(list(graph.triples()))):
        for j in range(0, len(list(graph.triples())[0])):
            if (list(graph.triples())[i][j][1] == 'NOUN'):
                arrGraph.append(list(graph.triples())[i][j][0])
    arrGraph = set(arrGraph)
    if (len(arrGraph) == 0):
        tokenizedA.append('!');
    else:
        for nArrGraph in arrGraph:
            tokenizedA.append(tokenizer.encode(nArrGraph, add_special_tokens=False))
        tokenizedA = np.concatenate(tokenizedA, axis=0, out=None, dtype=None, casting="same_kind")
else:
    for k, v in bigSov.items(): 
        tokenizedA.append(tokenizer.encode(k, add_special_tokens=False))
        tokenizedA.append(tokenizer.encode(v['subj'], add_special_tokens=False))
        tokenizedA.append(tokenizer.encode(v['obj'], add_special_tokens=False))
    tokenizedA = np.concatenate(tokenizedA, axis=0, out=None, dtype=None, casting="same_kind")
    
print(tokenizedA)
print(type(tokenizedA))

[ 5081. 39974. 63570.]
<class 'numpy.ndarray'>


In [17]:
import pandas as pd

df = pd.read_excel('que_ans_excel_doc_main.xlsx')
df['tq'] = ''
df['ta'] = ''
df

q  \
0      Здравствуйте, подскажите пожалуйста, я обучала...   
1      Здраствуйте, если ты уже зачислен на первый ку...   
2      Здравствуйте! В магистратуре можно ли поменять...   
3      Добрый день, а можно узнать стипендию на факул...   
4      Здравствуйте, как получить справку для родител...   
...                                                  ...   
44894  Скажите пожалуйста,какие нужно в этом году сда...   
44895  какие мне экзамены нужно сдавать по егэ на спе...   
44896                                 Если да, то когда?   
44897  Поступать нужно по сертификату о сдаче ЕГЭ или...   
44898  Какие языки изучают студенты на специальности ...   

                                                       a tq ta  
0      Здравствуйте. По данному вопросу обратитесь по...        
1      Здравствуйте. Вам необходимо сообщить об этом ...        
2      Здравствуйте. По данному вопросу обратитесь по...        
3      Здравствуйте. По данному вопросу вам необходим...        
4      Здравствуйте. По данному вопросу вам необходим...        
...                                                  ... .. ..  
44894  Надо сдавать экзамены по русскому языку, матем...        
44895  Надо сдавать в форме и по материалам ЕГЭ матем...        
44896  В город Семей Республики Казахстан выезд прием...        
44897  Свидетельство ЕГЭ с результатами экзаменов по ...        
44898          Факультативно-испанский(или итальянский).        

[44899 rows x 4 columns]

In [18]:
def fullExColl(text, n, cell):
    arrParsed = []
    longParsed = ''

    sent = str(text)
    print(sent)
    sent = re.sub("\s\s+", ' ', sent)
    sent = sent.lower()
    sent = sent.strip()
    sent = sent.replace(u'\xa0', u' ')
    sentS = re.split(";|! |\?|\. ", sent)
    sentS = list(filter(None, sentS))

    for nSentS in sentS:
        nSentS = re.sub(r'[^\w\s]','', nSentS) 

        pipeline = Pipeline(model, 'tokenize', Pipeline.DEFAULT, Pipeline.DEFAULT, Pipeline.DEFAULT)
        parsed = pipeline.process(nSentS)

        # костыли для dependency graph
        parsed = '\n'.join([line for line in parsed.split('\n') if not line.startswith('#')])
        parsed = parsed.replace('\troot\t', '\tROOT\t')

        if (len(longParsed) < len(parsed)):
            longParsed = parsed

        arrParsed.append(parsed)
    arrParsed = list(filter(None, arrParsed))

    arrSov = []
    for nArrParsed in arrParsed:
        sov = get_sov(nArrParsed)
        arrSov.append(sov)

    bigSov = arrSov[0]
    if (len(arrSov) > 1):
        for i in range(1, len(arrSov)):
            bigSov = { **bigSov, ** arrSov[i] }

    tokenizedA = []
    if (bigSov == {}):
        arrGraph = []
        graph = DependencyGraph(tree_str=longParsed)
        for i in range(0, len(list(graph.triples()))):
            for j in range(0, len(list(graph.triples())[0])):
                if (list(graph.triples())[i][j][1] == 'NOUN'):
                    arrGraph.append(list(graph.triples())[i][j][0])
        arrGraph = set(arrGraph)
        if (len(arrGraph) == 0):
            tokenizedA.append('!');
        else:
            for nArrGraph in arrGraph:
                tokenizedA.append(tokenizer.encode(nArrGraph, add_special_tokens=False))
            tokenizedA = np.concatenate(tokenizedA, axis=0, out=None, dtype=None, casting="same_kind")
    else:
        for k, v in bigSov.items(): 
            tokenizedA.append(tokenizer.encode(k, add_special_tokens=False))
            tokenizedA.append(tokenizer.encode(v['subj'], add_special_tokens=False))
            tokenizedA.append(tokenizer.encode(v['obj'], add_special_tokens=False))
        tokenizedA = np.concatenate(tokenizedA, axis=0, out=None, dtype=None, casting="same_kind")

    df[cell][n] = tokenizedA

In [19]:
model = Model.load('russian-ud-2.0-170801.udpipe')
tokenizer = AutoTokenizer.from_pretrained("cointegrated/rubert-tiny2")

# fullExColl(df['q'][0], 0, 'tq')

for i in range(0, len(df)):
    fullExColl(df['q'][i], i, 'tq')
#     fullExColl(df['a'][i], i, 'ta')

Здравствуйте, подскажите пожалуйста, я обучалась в нгту, кампусная карта уже была, поступила в магистратуру, заполнила данные для кампусной карты, позже увидела, что не надо было заполнять, а можно просто разблокировать в бюро пропусков, мне теперь нужно новую кампусную карту забирать или можно просто разблокировать? То что я ввела данные для кампусной карты, ничего страшного?
Здраствуйте, если ты уже зачислен на первый курс, но планируешь учиться в другом вузе, как отчислиться?
Здравствуйте! В магистратуре можно ли поменять группу? или после зачисления уже не возможно?
Добрый день, а можно узнать стипендию на факультет прикладной математики и ифнорматики
Здравствуйте, как получить справку для родителей, информирующую что обучаюсь в университете?
Здравтвуйте, до какого числа надо оплачивать обучение
Добрый день! Абитуриент МАГ/261 ФЭН.1Мз. По состоянию на 29.08.2022 на сайте НГТУ отсутствует информация о зачислении по 2 этапу. Прошу проинформировать когда будет издан приказ о зачислени

Здравствуйте скажите уже больше недели прошло как мы подали документы на платное обучение, выбрали 10 августа день сдачи экзамена, почему-то нет английского языка на эту дату? И поменять мы не можем в лк. И тех поддержка не отвечает? Как это можно сделать чтоб все три предмета были в один день?
Здравствуйте, подскажите, пожалуйста, обновлены ли списки вакантных мест? Написано, что есть 3 места на социологию( очное ) и 1 значное. Так ли это?
Добрый день! Можно детей из одного класса записать в одну группу, они поступили на один факультете, где будет, видимо 3 группы?
Здравсвуйте, если подал согласие на 1 специальность, только на бюджет, при не зачислении на бюждет, буду ли переведен на контракт?
Добрый день. Ответьте пожалуйста такая ситуация, прохожу на бюджет, но позвонили из Москвы и прохожу туда на бюджет, как я могу забрать оригинал аттестата
Здравствуйте. Меня интересует разница направлений ФПМИ 1 и ФПМИ 2. К кому конкретно обращаться?
Здравствуйте! Подал согласие на зачисление на

во сколько будет приказ о зачислении от 30.07?
Здравствуйте! Могу ли я расчитывать на место в общежитие, если я иностранец и поступаю на контракт?
здравствуйте. на данный момент я живу не в нск и мне довольно проблематично сдать лично в приемную комиссию оригинал документов. смогут ли меня зачислить с электронными копиями документов или я не смогу участвовать в конкурсе без оригинал документов? и еще вопрос: у меня отклонили согласие на зачисление с причиной "недействительно", что это значит и как можно исправить ситуацию?
Здравствуйте, какая будет стипендия у меня на первом курсе , если у меня 251 балл за егэ , 9 баллов за индивидуальные достижения и я поступила по олимпиаде
Здравствуйте. Нужен ли реферат для поступления в аспирантуру? Или можно предоставить свою научную статью (объём прим. 30 стр.)? Если нужен реферат, то где можно посмотреть требования к содержанию и оформлению? Также ещё интересует, учитывается ли в качестве индивидуальных достижений статьи РИНЦ? (в приёмной комисс

Здравстуйте могу ли я потом с платного обучения перейти на бюджет ?
Здравствуйте. Подскажите, пожалуйста, если я заключу договор на платные образовательные услуги и внесу оплату за семестр, а позднее выяснится, что по баллам я прохожу на бюджет. Можно будет перевестись на бюджет и вернуть уплаченные деньги?
В Математике я получила 54 балла, а в рейтинге стоит что у меня 52 балла по этому предмету. И результат физики ещё не известен
Здравствуйте, можно ли после окончания медицинского колледжа по специальности фармация поступить в нгту на психолога без результатов егэ, а просто по вступительным внутренним экзаменам? Или нужно заново сдавать егэ?
Добрый день,приёмная комиссия требует заверенный перевод моего аттестата хотя он у меня так на русском языку?
Здравствуйте, подскажите, пожалуйста, какой второй иностранный язык на специальности "Переводчик английского языка и русского жестового языка"? Будут языки на выбор или какой-то конкретный?
Можно ли отдать аттестат родственнику, чтобы он 

Здравствуйте! Есть ли бюджетные места на профиль "Сетевые информационные технологии" направления "Информатика и вычислительная техника"? Когда подавал документы через личный кабинет, хотел выбрать это направление, но там был только контракт, а на сайте увидел, что бюджетные места есть. Если бюджет всё же есть, то как мне теперь можно поменять одно из выбранных направлений (заявление уже принято и я есть в списках) на ИВТ с этим профилем?
Здравствуйте! Подскажите, пожалуйста, у вас есть курсу или факультет по психологии по заочной форме обучения?
Сдал экзамены. Когда ждать зачисление?
При электронной подаче документов в разделе "Список документов" под номер 1 требуется заявление. Подскажите, пожалуйста, что именно это за заявление.
Здравствуйте, подскажите пожалуйста когда будет известно поступили на бюджет или нет?
До какого нужно подать согласие на зачисление по особой квоте? Я запутался, до 28 июля, или до 4 августа?
Здравствуйте! поступаю по целевому обучению, документы подала через

...

Спасибо за ответ. Но это не то, что мне нужно. Я поступаю на заочное, ЕГЭ сдавать не надо, т.к. школу закончил в 1998г. Мне нужно посмотреть примеры тестов, чтобы знать к чему готовиться. Где я могу с ними ознакомиться?
Здравствуйте! 10-12 апреля я сдавал вступительные экзамены в г. Темиртау( РК). Мой результат: мат.-76, рус.яз.- 84, общест.-92. Каковы мои шансы поступить на Факультет Бизнеса( спец. " Прикладная Информатика") или на Факультет Прикладной Математики и Информатики ( спец. та же) ? Есть ли на эту специальность бюджетные места на каком-либо из этих факультетах? 
Обязательно ли проходить обучение и тестирование по рксскому языку для граждан СНГ? Если абитуриент поступил на бюджетную форму обучения, есть ли для него какие либо уступки со стороны университета по проживанию?
Здравствуйте! Подскажите пожалуйста где и когда будут вручать грамоты Всесибирской олимпиады
В городе Новосибирске такие учебные заведения как НГТУ и НГУ, создали абсурдную ситуацию, на специальность «Инфор

Здравствуйте, я вот задавал вопрос по поводу замены хотябы на одной спеуиальности физики на информатику...данный вопрос как нибуль решается, или ни каких изменений больше не будет в перечне ? 
здравствуйте!можно ли поступить к вам на специальность "Биомедицинская инженерия"?
скажите, пожалуйста, какой конкурс на место на ФМА "Автоматизация технологических процессов и производств в нефтяной и газовой промышленности"?
А почему Вы убрали вступительный экзамен по информатике, а другие ВУЗы нет?Спасибо!
Скажите насколько это реально поступить на бюджетное место АВТФ, не имея сертификат олимпиад? 
Здравствуйте.На какие факультеты НГТУ можно поступить по результатам всесибирской олимпиады.
Добрый день! Уважаемый Борис Борисович, Вы вероятно острее других в НГТУ почувствовали тревожное состояние абитуриентов связанных с решением совета деканов Вашего вуза об изменении перечня сдаваемых экзаменов. Мой сын также планировал поступление в Ваш вуз, но теперь это скорее всего это не возможно, по изв

Когда будут известны окончательные результаты Всесибирской олимпиады?
Скажите, пожалуйста, какова оплата на ФБ?
Есть ли возможность поступить на бюджетное отделение на ФБ?и если есть, то сколько бюджетных мест предоставляется?
Здравствуйте, я хочу узнать на ФБ ВСЕ специальности являются бакалаврами? 
когда будут известно решение о зачислении в нгту по результатам олимпиады по математике, которая проходила 22 марта в нгту? обещали же через 2 недели, с чем связана задержка?
Здравствуйте, вот на такие специальности как электроника и подобные не спорю ведущий предмет являеться физика, а на такие специльности как програмирование и компютерная безопасность мне кажеться являеться информатика...но как бы вопрос в принципе в другом: можете поставить хотя бы на пару специальностей вступительный не физику а информатику, министерство же сказала три экзамена выбрать, а выбор за вами физика или информатика, а то с информатикой вообще в ваш вуз не поступить, а так бы шансы уровняли, у кого то физика,

Добрый день! меня волнует вопрос по специальностям ФЭН. Где работают выпускники окончившие специальность Электрические станции? где можно найти информацию по данной специальности? 
В результатах Всесибирской олимпиады по математике непонятно, что означает "НГУ"? Если это те, кто получит преимущество при поступлении, то почему некоторые результаты ниже, чем у тех, у кого "НГУ" отсутствует?
Я слышал, что при поступлении на ТЭФ, результаты олипиады учитываться не будут.. Это правда?
Здавствуйте.Я проходил тестирование на сайте дистанционного обучения и в связи с отключением электроэнергии не смог завершить тест, а позже зашёл пройти его уже нельзя.Что мне сделать в этом случае и как можно пересдать?
на ФГО бюджетные места со второго курса есть?
корпус и номер кабинета, чтобы можно было подойти и уточнить возникшие вопросы.
Если я правильно поняла, то на ФГО вообще нет бюджетных мест? Скажите, можно ли тогда сразу заплатить за все 5 лет обучения?
и могу ли я поступить на бюджет, являясь гр

У ВЫЕЗДНЫХ КОМИССИЙ В КАЗАХСТАН ЗАДАНИЯ ЕГЭ ИЛИ ОТ НГТУ?
Планируются ли бюджетные места в этом году на специальность "Теплоэнергетика"(ФЭН)?
Здравствуйте!!!Через какое время будут известны результаты тестирования, которое будет проводится в г.Усть-Каменогорске с 21 марта?спасибо
Есть ли бюджеты на факультет бизнеса в 2009?
Здравствуйте, приедет ли в этом году приёмная комисссия в г. Усть-Илимск?
Как расчитывают проходной бал? 
Где можно найти пробные тесты 2009 года по английскому, русскому и математике???
Здравствуйте, хотела поинтересоваться, заканчиваю среднее профессиональное образование, хочу поступить на очное отделение ФГО (психилогия), могу ли я поступить без вступительных экзаменов и могут ли зачислить на 2й курс?
На дне открытых дверей была озвучена информация по поводу Всесибирской олимпиады.Когда она будет проводиться и как можно попасть в число ее участников?
Средний балл аттестата будет учитываться при поступлении?
Могу ли я учавствовать в олимпиаде только по одному предм

In [20]:
df

q  \
0      Здравствуйте, подскажите пожалуйста, я обучала...   
1      Здраствуйте, если ты уже зачислен на первый ку...   
2      Здравствуйте! В магистратуре можно ли поменять...   
3      Добрый день, а можно узнать стипендию на факул...   
4      Здравствуйте, как получить справку для родител...   
...                                                  ...   
44894  Скажите пожалуйста,какие нужно в этом году сда...   
44895  какие мне экзамены нужно сдавать по егэ на спе...   
44896                                 Если да, то когда?   
44897  Поступать нужно по сертификату о сдаче ЕГЭ или...   
44898  Какие языки изучают студенты на специальности ...   

                                                       a  \
0      Здравствуйте. По данному вопросу обратитесь по...   
1      Здравствуйте. Вам необходимо сообщить об этом ...   
2      Здравствуйте. По данному вопросу обратитесь по...   
3      Здравствуйте. По данному вопросу вам необходим...   
4      Здравствуйте. По данному вопросу вам необходим...   
...                                                  ...   
44894  Надо сдавать экзамены по русскому языку, матем...   
44895  Надо сдавать в форме и по материалам ЕГЭ матем...   
44896  В город Семей Республики Казахстан выезд прием...   
44897  Свидетельство ЕГЭ с результатами экзаменов по ...   
44898          Факультативно-испанский(или итальянский).   

                                                      tq ta  
0      [38209.0, 5750.0, 343.0, 64617.0, 38645.0, 560...     
1             [45783.0, 33649.0, 733.0, 33980.0, 2993.0]     
2                    [5081.0, 42173.0, 15234.0, 14159.0]     
3                     [5081.0, 4045.0, 30799.0, 68380.0]     
4           [18348.0, 53039.0, 31590.0, 48341.0, 1046.0]     
...                                                  ... ..  
44894  [21211.0, 33013.0, 872.0, 8656.0, 41999.0, 451...     
44895  [13267.0, 21211.0, 21211.0, 45108.0, 20284.0, ...     
44896                                                [!]     
44897               [38600.0, 21211.0, 41999.0, 45108.0]     
44898                                 [52166.0, 24081.0]     

[44899 rows x 4 columns]

In [13]:
df.to_excel("13112022_main_full.xlsx") 